# Project Phase 3: Video Moment Detection

## Connection to Opensearch index

In [58]:
import pprint as pp
import requests

host = 'localhost'
port = 9200

user = 'admin' # Add your user name here.
password = 'a.Zerty12.3' # Add your user password here. For testing only. Don't store credentials in code. 
index_name = user

In [59]:
import pprint as pp
from opensearchpy import OpenSearch
from opensearchpy import helpers

# Create the client with SSL/TLS enabled, but hostname verification disabled.
client = OpenSearch(
    hosts = [{'host': host, 'port': port}],
    http_auth = (user, password),
    use_ssl = True,
    verify_certs = False,
)

if client.indices.exists(index_name):

    resp = client.indices.open(index = index_name)
    print(resp)

    print('\n----------------------------------------------------------------------------------- INDEX SETTINGS')
    settings = client.indices.get_settings(index = index_name)
    pp.pprint(settings)

    print('\n----------------------------------------------------------------------------------- INDEX MAPPINGS')
    mappings = client.indices.get_mapping(index = index_name)
    pp.pprint(mappings)

    print('\n----------------------------------------------------------------------------------- INDEX #DOCs')
    print(client.count(index = index_name))
else:
    print("Index does not exist.")

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/opensearchpy/connection/http_urllib3.py:214: UserWarning: Connecting to https://localhost:9200 using SSL with verify_certs=False is insecure.
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


{'acknowledged': True, 'shards_acknowledged': True}

----------------------------------------------------------------------------------- INDEX SETTINGS
{'admin': {'settings': {'index': {'creation_date': '1747233421129',
                                  'knn': 'true',
                                  'number_of_replicas': '0',
                                  'number_of_shards': '4',
                                  'provided_name': 'admin',
                                  'refresh_interval': '-1',
                                  'replication': {'type': 'DOCUMENT'},
                                  'uuid': '8vtb84HURpa0s4tsF88OQg',
                                  'version': {'created': '136347827'}}}}}

----------------------------------------------------------------------------------- INDEX MAPPINGS
{'admin': {'mappings': {'properties': {'caption_bow': {'analyzer': 'standard',
                                                       'type': 'text'},
                           

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

## Video downloading

In [60]:
import os
import subprocess

# Directory where videos will be saved
download_path = "./videos_part3"
os.makedirs(download_path, exist_ok=True)  # Create folder if it doesn't exist

video_url = "https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c" # Replace with the actual video URL
video_id = video_url.split("=")[1]  # Extracted video ID from the URL
#print(f"Video ID: {video_id}")

# Loop through each video in the top 10
output_template = os.path.join(download_path, f"{video_id}.mp4")

try:
    print(f"Downloading: {video_url}")
    subprocess.run(["yt-dlp", "-o", output_template, video_url], check=True)
    print(f"Downloaded: {output_template}")
except subprocess.CalledProcessError:
    print(f"Failed to download {video_id}.")

Downloading: https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c
[youtube] Extracting URL: https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c
[youtube] daxodF_Pnzg: Downloading webpage
[youtube] daxodF_Pnzg: Downloading tv client config
[youtube] daxodF_Pnzg: Downloading player f203bbc8
[youtube] daxodF_Pnzg: Downloading tv player API JSON
[youtube] daxodF_Pnzg: Downloading ios player API JSON


         player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js
         n = E32QDlE2WlCxd6Mk ; player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js
         player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js
         n = qdpShy9xFfioZ8Ji ; player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js
         player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js
         n = BM53-nY72TI6Rpu_ ; player = https://www.youtube.com/s/player/f203bbc8/player_ias.vflset/en_US/base.js


[youtube] daxodF_Pnzg: Downloading m3u8 information
[info] daxodF_Pnzg: Downloading 1 format(s): 616+234
[download] ./videos_part3/GM0lJFcjXopRpQ2c.mp4 has already been downloaded
Downloaded: ./videos_part3/GM0lJFcjXopRpQ2c.mp4


## Frames extraction

In [61]:
import av
import av.datasets
import os

output_folder = "./frames_part3"
input_folder = "./videos_part3"
video = "/GM0lJFcjXopRpQ2c.mp4"
# File name without extension
filename = os.path.splitext(video)[0]
if not os.path.isdir(output_folder + "/" + filename):
    os.makedirs(output_folder + "/" + filename)
with av.open(input_folder + video) as container:
    stream = container.streams.video[0]
    # We want 2 frame per second
    fps = stream.average_rate
    interval = int(round(fps*0.5))
    #print(fps)
    cpt = 0
    for i,frame in enumerate(container.decode(stream)):
        if i % interval == 0:
            frame.to_image().save(output_folder+"/"+filename+"/"+str(cpt*(0.5))+".jpg", quality=80)
            cpt += 1

## Opensearch index update

In [62]:
# Give every documents added to the index: just to check how the index looks like
client.indices.refresh(index=index_name)
query = {
    "query": {
        "match_all": {}
    },
    "size": 100  # Adjust the number to see more results if needed
}

response = client.search(
    index=index_name,
    body=query
)

# Print the total number of documents and some of the documents
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])  # Print the source of each document

Total hits: 1709
{'video_id': 'o1WPnnvs00I', 'moment_description': 'A man is playing a flute in front of a microphone.', 'frame_path': './frames/o1WPnnvs00I/3.jpg', 'caption_bow': ['front', 'in', 'playing', 'of', 'flute', 'a', 'microphone.', 'man', 'is'], 'caption_vec': [0.0338418148458004, -0.006800513714551926, -0.0009816654492169619, -0.08312956988811493, -0.13254886865615845, 0.035441670566797256, 0.0748010203242302, -0.03751223161816597, 0.014732320792973042, -0.028699280694127083, -0.03486842289566994, -0.06718401610851288, -0.12319913506507874, -0.016461659222841263, 0.0722806304693222, -0.06964749097824097, -0.014246728271245956, 0.004854982253164053, 0.056748293340206146, -0.030198318883776665, 0.02052198350429535, 0.11677198112010956, -0.04872555285692215, -0.044588446617126465, 0.056011177599430084, 0.0292632095515728, -0.035124290734529495, 0.040314026176929474, 0.0831347405910492, 0.006201791111379862, 0.058498553931713104, -0.024395329877734184, 0.03162509202957153, -0.00

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


In [63]:
import os

frames_directory = "./frames_part3/" 

# For each frame in the directory, create a document and add it to the index
for subfolder in os.listdir(frames_directory):
    subfolder_path = os.path.join(frames_directory, subfolder)

    # Check if the subfolder is indeed a directory
    if os.path.isdir(subfolder_path):
        video_id = subfolder
        print(video_id + " subfolder found.")

        # Iterate through each frame in the subfolder
        for frame in os.listdir(frames_directory + subfolder):
            frame_path = os.path.join(frames_directory + subfolder, frame)
            print(frame_path)
            
            # Check the file extension to ensure it's an image
            if frame.lower().endswith(('.png', '.jpg', '.jpeg')):
                document = {
                    "video_id": video_id,
                    "moment_description": None,
                    "frame_path": frame_path,
                    "caption_bow": None,
                    "caption_vec": None,
                    "visual_description_vec": None,
                    "frame_vec": None,
                    "end_timestamp": None,
                    "start_timestamp": None,
                    "video_length": None,
                }

                # Add the document to the index
                response = client.index(
                    index=index_name,
                    body=document
                )
                #print(f"Document added for frame: '{frame}':", response)


GM0lJFcjXopRpQ2c subfolder found.
./frames_part3/GM0lJFcjXopRpQ2c/182.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/63.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/95.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/95.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/35.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/92.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/20.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/118.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/105.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/103.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/6.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/44.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/93.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/171.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/72.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/115.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/132.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/80.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/150.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/104.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/117.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/10.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/147.5.jpg
./frames_part

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

./frames_part3/GM0lJFcjXopRpQ2c/184.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/31.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/40.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/22.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/19.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/173.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/143.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/23.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/129.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/21.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/168.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/156.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/75.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/155.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/149.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/26.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/57.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/111.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/36.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/179.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/25.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/72.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/120.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/9.0.jpg
./fram

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

./frames_part3/GM0lJFcjXopRpQ2c/69.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/99.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/53.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/57.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/14.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/67.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/8.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/49.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/107.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/96.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/45.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/158.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/173.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/93.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/68.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/29.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/145.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/60.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/20.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/186.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/162.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/26.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/27.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/137.0.jpg
./frames_p

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

./frames_part3/GM0lJFcjXopRpQ2c/140.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/187.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/86.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/169.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/128.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/84.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/1.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/122.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/23.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/46.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/176.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/75.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/73.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/65.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/178.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/25.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/62.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/98.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/82.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/168.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/142.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/39.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/175.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/50.5.jpg
./frame

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

./frames_part3/GM0lJFcjXopRpQ2c/60.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/97.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/88.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/80.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/81.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/127.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/138.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/41.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/48.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/92.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/43.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/155.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/148.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/132.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/185.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/24.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/157.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/42.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/102.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/38.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/13.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/90.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/31.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/78.5.jpg
./frames

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

In [64]:
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

Total hits: 387
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/35.0.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': None, 'end_timestamp': None, 'start_timestamp': None, 'video_length': None}
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/92.0.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': None, 'end_timestamp': None, 'start_timestamp': None, 'video_length': None}
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/132.5.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': None, 'end_timestamp': None, 'start_timestamp': None, 'video_length': None}
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/104.0.jpg', 'caption_bow': No

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


## Captions generations

## Captions encoding

### Frame embedding and index update (if needed)

In [67]:
import torch
import numpy as np
from PIL import Image
from transformers import CLIPProcessor, CLIPModel

# Load the clip Model and Processor
model_name = "openai/clip-vit-base-patch32"
model = CLIPModel.from_pretrained(model_name)
processor = CLIPProcessor.from_pretrained(model_name)

# Encoding function
def encode_image(image_path):
    image = Image.open(image_path).convert("RGB") # Ensure the image is in RGB format

    # Prepare the image for the model
    inputs = processor(images=image, return_tensors="pt", truncation=True, max_length=77)

    # Encode the image to get the embedding
    with torch.no_grad():
        image_features = model.get_image_features(**inputs)
    
    # Normalize the image embedding
    image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)

    return image_features.numpy()[0]


# Iterate on the documents
query = {
    "query": {
            "bool": {
                "must_not": {
                    "exists": {
                        "field": "moment_description"
                    }
                }
            }
        },
}

# Retrieve all documents from the index
response = client.search(index=index_name, body=query, size=3000)
documents = response["hits"]["hits"]
# Add the embedding to each document
for doc in documents:
    doc_id = doc["_id"]  # ID document

    image_path = doc["_source"]["frame_path"]  # Get the image path from the document
    #print(image_path)
    embedding = encode_image(image_path)  # Get the embedding for the image

    # Update the document with the new field
    update_body = {
        "doc": {
            "frame_vec": embedding
        }
    }
    update_response = client.update(index=index_name, id=doc_id, body=update_body)

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina

In [68]:
# Check the embeddings were added correctly
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

Total hits: 387
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/35.0.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': [0.009502447210252285, 0.030533291399478912, 0.0172860249876976, 0.04556897655129433, -0.05109778046607971, -0.03440028056502342, 0.01571556366980076, -0.001508246292360127, 0.022760536521673203, -0.05047549307346344, -0.012603161856532097, -0.03577895835042, 0.04434818774461746, 0.028946228325366974, -0.026700899004936218, 0.015574815683066845, -0.11283522844314575, -0.02891222946345806, 0.046853747218847275, -0.030611129477620125, -0.08348439633846283, 0.023410145193338394, -0.003400359768420458, 0.014824523590505123, 0.030492426827549934, 0.027299225330352783, -0.018584618344902992, 0.012025921605527401, 0.008547146804630756, -0.021522577852010727, 0.007875210605561733, 0.024618936702609062, -0.019779697060585022, -0.002050386741757393, 0.01903236284852028, 0.03201

/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/home/lina/miniconda3/envs/nlp-cv-ir/lib/python3.9/site-packages/urllib3/connectionpool.py:1064: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


### Caption embedding

In [ ]:
import torch
import numpy as np
from PIL import Image
from transformers import CLIPProcessor, CLIPModel

# Load the clip Model and Processor
model_name = "openai/clip-vit-base-patch32"
model = CLIPModel.from_pretrained(model_name)
processor = CLIPProcessor.from_pretrained(model_name)

# Encoding function
def encode_text(caption):

    inputs = processor(text=caption, return_tensors="pt", padding=True, truncation=True, max_length=77)

    # Encode the caption to get the embedding
    with torch.no_grad():
        embedding = model.get_text_features(**inputs)
    
    # Normalize the caption embedding
    embedding = embedding / embedding.norm(dim=-1, keepdim=True)

    return embedding.numpy()[0]


# Iterate on the documents
query = {
    "query": {
            "bool": {
                "must_not": {
                    "exists": {
                        "field": "visual_description_vec"
                    }
                }
            }
        },
}
# Retrieve all documents from the index
response = client.search(index=index_name, body=query, size=2000)
documents = response["hits"]["hits"]
# Add the embedding of the description to each document that have one
for doc in documents:
    doc_id = doc["_id"]  # ID document

    caption = doc["_source"]["moment_description"]  # Get the caption from the document
    
    if not caption == None:
        embedding = encode_text(caption)  # Get the embedding for the caption

        # Update the document with the new field
        update_body = {
            "doc": {
                "visual_description_vec": embedding
            }
        }
        update_response = client.update(index=index_name, id=doc_id, body=update_body)

In [ ]:
# Check the embeddings were added correctly
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

## Regroupment based on clustering

## Frames fusionning